<a href="https://colab.research.google.com/github/vsairam-uc/GenAI-and-LLM/blob/main/gpt_variation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!kaggle datasets download -d <id>/wine-reviews && echo 'Unzipping...' && unzip -q -o wine-reviews.zip -d /wine-reviews && rm wine-reviews.zip && echo '🚀 Done!'

Dataset URL: https://www.kaggle.com/datasets/zynicide/wine-reviews
License(s): CC-BY-NC-SA-4.0
100% 50.9M/50.9M [00:03<00:00, 22.5MB/s]
100% 50.9M/50.9M [00:03<00:00, 14.4MB/s]
Unzipping...
🚀 Done!


In [34]:
%load_ext autoreload
%autoreload 2
import numpy as np
import json
import re
import string
from IPython.display import display, HTML

import tensorflow as tf
from tensorflow.keras import layers, models, losses, callbacks

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Parameters

In [35]:
VOCAB_SIZE = 10000
MAX_LEN = 80
EMBEDDING_DIM = 256
KEY_DIM = 256
N_HEADS = 2
FEED_FORWARD_DIM = 256
VALIDATION_SPLIT = 0.2
SEED = 42
LOAD_MODEL = False
BATCH_SIZE = 32
EPOCHS = 50

## Load Data

In [36]:
with open("/wine-reviews/winemag-data-130k-v2.json") as json_data:
    wine_data = json.load(json_data)

In [37]:
wine_data[10]

{'points': '87',
 'title': 'Kirkland Signature 2011 Mountain Cuvée Cabernet Sauvignon (Napa Valley)',
 'description': 'Soft, supple plum envelopes an oaky structure in this Cabernet, supported by 15% Merlot. Coffee and chocolate complete the picture, finishing strong at the end, resulting in a value-priced wine of attractive flavor and immediate accessibility.',
 'taster_name': 'Virginie Boone',
 'taster_twitter_handle': '@vboone',
 'price': 19,
 'designation': 'Mountain Cuvée',
 'variety': 'Cabernet Sauvignon',
 'region_1': 'Napa Valley',
 'region_2': 'Napa',
 'province': 'California',
 'country': 'US',
 'winery': 'Kirkland Signature'}

In [38]:
# Filter the dataset
filtered_data = [
    "wine review : "
    + x["country"]
    + " : "
    + x["province"]
    + " : "
    + x["variety"]
    + " : "
    + x["description"]
    for x in wine_data
    if x["country"] is not None
    and x["province"] is not None
    and x["variety"] is not None
    and x["description"] is not None
]

In [39]:
n_wines = len(filtered_data)
print(f"{n_wines} recipes loaded")

129907 recipes loaded


In [40]:
example = filtered_data[25]
print(example)

wine review : US : California : Pinot Noir : Oak and earth intermingle around robust aromas of wet forest floor in this vineyard-designated Pinot that hails from a high-elevation site. Small in production, it offers intense, full-bodied raspberry and blackberry steeped in smoky spice and smooth texture.


## Tokenize the data

In [41]:
def pad_punctuation(s):
    s = re.sub(f"([{string.punctuation}, '\n'])", r" \1 ", s)
    s = re.sub(" +", " ", s)
    return s


text_data = [pad_punctuation(x) for x in filtered_data]

In [42]:
# Display an example of a recipe
example_data = text_data[25]
example_data

'wine review : US : California : Pinot Noir : Oak and earth intermingle around robust aromas of wet forest floor in this vineyard - designated Pinot that hails from a high - elevation site . Small in production , it offers intense , full - bodied raspberry and blackberry steeped in smoky spice and smooth texture . '

In [43]:
text_ds = (
    tf.data.Dataset.from_tensor_slices(text_data)
    .batch(BATCH_SIZE)
    .shuffle(1000)
)

In [44]:
vectorize_layer = layers.TextVectorization(
    standardize="lower",
    max_tokens=VOCAB_SIZE,
    output_mode="int",
    output_sequence_length=MAX_LEN + 1,
)

In [45]:
# Adapt the layer to the training set
vectorize_layer.adapt(text_ds)
vocab = vectorize_layer.get_vocabulary()

In [46]:
for i, word in enumerate(vocab[:10]):
    print(f"{i}: {word}")

0: 
1: [UNK]
2: :
3: ,
4: .
5: and
6: the
7: wine
8: a
9: of


In [47]:
example_tokenised = vectorize_layer(example_data)
print(example_tokenised.numpy())

[   7   10    2   20    2   29    2   43   62    2   55    5  243 4145
  453  634   26    9  497  499  667   17   12  142   14 2214   43   25
 2484   32    8  223   14 2213  948    4  594   17  987    3   15   75
  237    3   64   14   82   97    5   74 2633   17  198   49    5  125
   77    4    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0]


## Create the Training Set

In [48]:
def prepare_inputs(text):
    text = tf.expand_dims(text, -1)
    tokenized_sentences = vectorize_layer(text)
    x = tokenized_sentences[:, :-1]
    y = tokenized_sentences[:, 1:]
    return x, y


train_ds = text_ds.map(prepare_inputs)

In [49]:
example_input_output = train_ds.take(1).get_single_element()

In [50]:
# Example Input
example_input_output[0][0]

<tf.Tensor: shape=(80,), dtype=int64, numpy=
array([   7,   10,    2,   40,    2,  144,    2,  163,    2,   12, 1939,
        163,  162,   11,   16,    9,   36,    3,   74,    5,  346,  888,
         49,    4,   15,  211,   87,   30,    3,  160,    5,  816,    3,
         11,    8,  467,   14,  597,  840,    4,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0])>

In [51]:
# Example Output (shifted by one token)
example_input_output[1][0]

<tf.Tensor: shape=(80,), dtype=int64, numpy=
array([  10,    2,   40,    2,  144,    2,  163,    2,   12, 1939,  163,
        162,   11,   16,    9,   36,    3,   74,    5,  346,  888,   49,
          4,   15,  211,   87,   30,    3,  160,    5,  816,    3,   11,
          8,  467,   14,  597,  840,    4,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0])>

## Create the causal attention mask function

In [52]:
def causal_attention_mask(batch_size, n_dest, n_src, dtype):
    i = tf.range(n_dest)[:, None]
    j = tf.range(n_src)
    m = i >= j - n_src + n_dest
    mask = tf.cast(m, dtype)
    mask = tf.reshape(mask, [1, n_dest, n_src])
    mult = tf.concat(
        [tf.expand_dims(batch_size, -1), tf.constant([1, 1], dtype=tf.int32)], 0
    )
    return tf.tile(mask, mult)


np.transpose(causal_attention_mask(1, 10, 10, dtype=tf.int32)[0])

array([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
       [0, 1, 1, 1, 1, 1, 1, 1, 1, 1],
       [0, 0, 1, 1, 1, 1, 1, 1, 1, 1],
       [0, 0, 0, 1, 1, 1, 1, 1, 1, 1],
       [0, 0, 0, 0, 1, 1, 1, 1, 1, 1],
       [0, 0, 0, 0, 0, 1, 1, 1, 1, 1],
       [0, 0, 0, 0, 0, 0, 1, 1, 1, 1],
       [0, 0, 0, 0, 0, 0, 0, 1, 1, 1],
       [0, 0, 0, 0, 0, 0, 0, 0, 1, 1],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 1]], dtype=int32)

## Create a Transformer Block layer

In [53]:
class TransformerBlock(layers.Layer):
    def __init__(self, num_heads, key_dim, embed_dim, ff_dim, dropout_rate=0.1):
        super(TransformerBlock, self).__init__()
        self.num_heads = num_heads
        self.key_dim = key_dim
        self.embed_dim = embed_dim
        self.ff_dim = ff_dim
        self.dropout_rate = dropout_rate
        self.attn = layers.MultiHeadAttention(
            num_heads, key_dim, output_shape=embed_dim
        )
        self.dropout_1 = layers.Dropout(self.dropout_rate)
        self.ln_1 = layers.LayerNormalization(epsilon=1e-6)
        self.ffn_1 = layers.Dense(self.ff_dim, activation="relu")
        self.ffn_2 = layers.Dense(self.embed_dim)
        self.dropout_2 = layers.Dropout(self.dropout_rate)
        self.ln_2 = layers.LayerNormalization(epsilon=1e-6)

    def call(self, inputs):
        input_shape = tf.shape(inputs)
        batch_size = input_shape[0]
        seq_len = input_shape[1]
        causal_mask = causal_attention_mask(
            batch_size, seq_len, seq_len, tf.bool
        )
        attention_output, attention_scores = self.attn(
            inputs,
            inputs,
            attention_mask=causal_mask,
            return_attention_scores=True,
        )
        attention_output = self.dropout_1(attention_output)
        out1 = self.ln_1(inputs + attention_output)
        ffn_1 = self.ffn_1(out1)
        ffn_2 = self.ffn_2(ffn_1)
        ffn_output = self.dropout_2(ffn_2)
        return (self.ln_2(out1 + ffn_output), attention_scores)

    def get_config(self):
        config = super().get_config()
        config.update(
            {
                "key_dim": self.key_dim,
                "embed_dim": self.embed_dim,
                "num_heads": self.num_heads,
                "ff_dim": self.ff_dim,
                "dropout_rate": self.dropout_rate,
            }
        )
        return config

## Create the Token and Position Embedding

In [54]:
class TokenAndPositionEmbedding(layers.Layer):
    def __init__(self, max_len, vocab_size, embed_dim):
        super(TokenAndPositionEmbedding, self).__init__()
        self.max_len = max_len
        self.vocab_size = vocab_size
        self.embed_dim = embed_dim
        self.token_emb = layers.Embedding(
            input_dim=vocab_size, output_dim=embed_dim
        )
        self.pos_emb = layers.Embedding(input_dim=max_len, output_dim=embed_dim)

    def call(self, x):
        maxlen = tf.shape(x)[-1]
        positions = tf.range(start=0, limit=maxlen, delta=1)
        positions = self.pos_emb(positions)
        x = self.token_emb(x)
        return x + positions

    def get_config(self):
        config = super().get_config()
        config.update(
            {
                "max_len": self.max_len,
                "vocab_size": self.vocab_size,
                "embed_dim": self.embed_dim,
            }
        )
        return config

## Build the Transformer model

In [55]:
inputs = layers.Input(shape=(None,), dtype=tf.int32)
x = TokenAndPositionEmbedding(MAX_LEN, VOCAB_SIZE, EMBEDDING_DIM)(inputs)
x, attention_scores = TransformerBlock(
    N_HEADS, KEY_DIM, EMBEDDING_DIM, FEED_FORWARD_DIM
)(x)
outputs = layers.Dense(VOCAB_SIZE, activation="softmax")(x)
gpt = models.Model(inputs=inputs, outputs=[outputs, attention_scores])
gpt.compile("adam", loss=[losses.SparseCategoricalCrossentropy(), None])

In [56]:
gpt.summary()

Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ input_layer_1 (InputLayer)           │ (None, None)                │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ token_and_position_embedding_1       │ (None, None, 256)           │       2,580,480 │
│ (TokenAndPositionEmbedding)          │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ transformer_block_1                  │ [(None, None, 256), (None,  │         658,688 │
│ (TransformerBlock)                   │ 2, None, None)]             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_5 (Dense)                      │ (None, None, 10000)         │       2,570,000 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 5,809,168 (22.16 MB)

 Trainable params: 5,809,168 (22.16 MB)

 Non-trainable params: 0 (0.00 B)

## Train the model

In [57]:
# Create a TextGenerator checkpoint
class TextGenerator(callbacks.Callback):
    def __init__(self, index_to_word, top_k=10):
        self.index_to_word = index_to_word
        self.word_to_index = {
            word: index for index, word in enumerate(index_to_word)
        }

    def sample_from(self, probs, temperature):
        probs = probs ** (1 / temperature)
        probs = probs / np.sum(probs)
        return np.random.choice(len(probs), p=probs), probs

    def generate(self, start_prompt, max_tokens, temperature):
        start_tokens = [
            self.word_to_index.get(x, 1) for x in start_prompt.split()
        ]
        sample_token = None
        info = []
        while len(start_tokens) < max_tokens and sample_token != 0:
            x = np.array([start_tokens])
            y, att = self.model.predict(x, verbose=0)
            sample_token, probs = self.sample_from(y[0][-1], temperature)
            info.append(
                {
                    "prompt": start_prompt,
                    "word_probs": probs,
                    "atts": att[0, :, -1, :],
                }
            )
            start_tokens.append(sample_token)
            start_prompt = start_prompt + " " + self.index_to_word[sample_token]
        print(f"\ngenerated text:\n{start_prompt}\n")
        return info

    def on_epoch_end(self, epoch, logs=None):
        self.generate("wine review", max_tokens=80, temperature=1.0)

In [58]:
tensorboard_callback = callbacks.TensorBoard(log_dir="./logs")

# Tokenize starting prompt
text_generator = TextGenerator(vocab)

In [59]:
gpt.fit(
    train_ds,
    epochs=EPOCHS,
    callbacks=[tensorboard_callback, text_generator],
)

Epoch 1/50
4060/4060 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step - loss: 2.5934
generated text:
wine review : italy : sicily & sardinia : mencía : ripe black fruit , clove and violet aromas come together with a whisper of tobacco and crushed herb while the tangy and fresh straightforward palate doles out ripe wild cherry , mint , clove and a hint of crushed raspberry . round tannins good , it ' s already delicious but polished and fresh . 

4060/4060 ━━━━━━━━━━━━━━━━━━━━ 132s 31ms/step - loss: 2.5933
Epoch 2/50
4058/4060 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step - loss: 1.9778
generated text:
wine review : us : washington : chardonnay : an outstanding value for this soft and creamy close , and the chalky minerality shows a quite round out apple and pear fruit . 

4060/4060 ━━━━━━━━━━━━━━━━━━━━ 97s 21ms/step - loss: 1.9778
Epoch 3/50
4060/4060 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step - loss: 1.8993
generated text:
wine review : chile : central valley : sauvignon blanc : dusty , green aromas of celery , jalapeño

## Generate text using the Transformer

In [60]:
def print_probs(info, vocab, top_k=5):
    for i in info:
        highlighted_text = []
        for word, att_score in zip(
            i["prompt"].split(), np.mean(i["atts"], axis=0)
        ):
            highlighted_text.append(
                '<span style="background-color:rgba(135,206,250,'
                + str(att_score / max(np.mean(i["atts"], axis=0)))
                + ');">'
                + word
                + "</span>"
            )
        highlighted_text = " ".join(highlighted_text)
        display(HTML(highlighted_text))

        word_probs = i["word_probs"]
        p_sorted = np.sort(word_probs)[::-1][:top_k]
        i_sorted = np.argsort(word_probs)[::-1][:top_k]
        for p, i in zip(p_sorted, i_sorted):
            print(f"{vocab[i]}:   \t{np.round(100*p,2)}%")
        print("--------\n")

### Temperature = 1

In [61]:
info = text_generator.generate(
    "wine review : us", max_tokens=250, temperature=1.0
)
print_probs(info, vocab)


generated text:
wine review : us : washington : syrah : this is along the top syrah from ciel du cheval and force majeure vineyards . blended luxuriously malbec , it ' s gorgeously complex and textural , showing a profound , lush core of cassis , animal cracker , and mineral notes that glide a , decanted or hours before unfolding . behind it ' s supple and seamless , it has fine layers of licorice , black pepper and herb . delicious , and licorice , streaks penetrate most extending from the long run finish . [UNK] the dark and hints of chocolate get at the power you can manage get along on like [UNK] right . this can get are on is worth find come ready to savor shine thanks from new from ever find . at stride let you get used get used let emerge from new get used from this emerge . 



::   	100.0%
of:   	0.0%
oregon:   	0.0%
in:   	0.0%
grosso:   	0.0%
--------



california:   	64.46%
washington:   	19.02%
oregon:   	10.29%
new:   	2.82%
virginia:   	2.0%
--------



::   	100.0%
-:   	0.0%
grosso:   	0.0%
other:   	0.0%
oregon:   	0.0%
--------



cabernet:   	21.56%
syrah:   	16.59%
bordeaux:   	13.71%
merlot:   	8.48%
red:   	6.5%
--------



...

manage:   	23.82%
to:   	11.36%
display:   	7.38%
from:   	5.0%
in:   	3.65%
--------



this:   	15.72%
the:   	13.52%
new:   	9.42%
.:   	8.85%
[UNK]:   	4.77%
--------



.:   	26.46%
new:   	15.52%
get:   	4.69%
emerge:   	2.33%
from:   	2.3%
--------



.:   	81.61%
;:   	5.48%
,:   	4.33%
from:   	2.58%
::   	2.42%
--------



:   	62.53%
drink:   	4.81%
the:   	2.74%
from:   	2.62%
it:   	2.55%
--------



In [64]:
info = text_generator.generate(
    "wine review : italy", max_tokens=250, temperature=1.0
)
print_probs(info, vocab)




generated text:
wine review : italy : veneto : red blend : aromas recalling dark berry , leather , tobacco and spice lead the nose along with notes of leather and dried berry . the extremely simple but well - made , it ' s rather shy , with vibrant acidity highlighting the firm with blackberry and chopped herb flavors wrapped in polished tannins . 



::   	100.0%
grosso:   	0.0%
-:   	0.0%
':   	0.0%
the:   	0.0%
--------



tuscany:   	36.15%
piedmont:   	18.23%
northeastern:   	13.41%
veneto:   	10.47%
sicily:   	8.31%
--------



::   	100.0%
grosso:   	0.0%
-:   	0.0%
other:   	0.0%
of:   	0.0%
--------



corvina:   	31.12%
glera:   	15.1%
red:   	15.0%
garganega:   	11.4%
prosecco:   	10.7%
--------



...

in:   	81.19%
up:   	11.46%
around:   	2.0%
tightly:   	1.4%
into:   	1.18%
--------



polished:   	14.74%
firm:   	13.43%
velvety:   	13.43%
astringent:   	5.31%
well:   	5.21%
--------



tannins:   	96.59%
,:   	2.29%
but:   	0.34%
wood:   	0.11%
yet:   	0.11%
--------



.:   	90.4%
and:   	8.2%
that:   	0.54%
on:   	0.48%
,:   	0.11%
--------



:   	70.44%
drink:   	16.75%
it:   	5.07%
enjoy:   	1.56%
give:   	1.05%
--------



In [65]:
info = text_generator.generate(
    "wine review : germany", max_tokens=250, temperature=1.0
)
print_probs(info, vocab)


generated text:
wine review : germany : mosel : riesling : a feather - light in mouthfeel , peach and honey flavors this auslese . just off dry , accented with earthy notes of coffee and cranberry acidity there seems to spread with flavors of sweet white tea and honey . otherwise , the finish is crisp and clean . 



::   	100.0%
grosso:   	0.0%
-:   	0.0%
of:   	0.0%
in:   	0.0%
--------



mosel:   	57.77%
rheinhessen:   	11.28%
rheingau:   	9.54%
pfalz:   	9.17%
franken:   	4.39%
--------



::   	92.82%
-:   	7.05%
[UNK]:   	0.02%
blanc:   	0.01%
grosso:   	0.01%
--------



riesling:   	94.76%
spätburgunder:   	0.78%
weissburgunder:   	0.67%
pinot:   	0.63%
mosel:   	0.43%
--------



...

long:   	22.04%
a:   	8.0%
marked:   	7.36%
dry:   	7.34%
brisk:   	5.44%
--------



and:   	71.31%
,:   	9.37%
.:   	8.64%
but:   	5.32%
with:   	1.48%
--------



clean:   	23.8%
long:   	6.0%
dry:   	4.32%
slightly:   	3.47%
lingering:   	2.81%
--------



.:   	60.59%
,:   	27.9%
as:   	2.83%
but:   	1.93%
and:   	1.62%
--------



:   	80.07%
drink:   	13.93%
a:   	0.77%
it:   	0.58%
enjoy:   	0.41%
--------



## Temperature = 0.5

In [66]:
info = text_generator.generate(
    "wine review : us", max_tokens=250, temperature=0.5
)
print_probs(info, vocab)


generated text:
wine review : us : california : merlot : a fine , everyday wine , with a good , dry , tannic and spicy , with rich , sweet , oaky flavors of blackberry , cherry and currant . it ' s a little too sweet , but could use some more time in the bottle . 



::   	100.0%
of:   	0.0%
oregon:   	0.0%
in:   	0.0%
grosso:   	0.0%
--------



california:   	89.65%
washington:   	7.81%
oregon:   	2.28%
new:   	0.17%
virginia:   	0.09%
--------



::   	100.0%
other:   	0.0%
grosso:   	0.0%
-:   	0.0%
of:   	0.0%
--------



pinot:   	35.66%
cabernet:   	32.35%
chardonnay:   	12.83%
zinfandel:   	8.38%
syrah:   	3.02%
--------



...

in:   	57.33%
to:   	34.73%
.:   	4.6%
for:   	2.44%
,:   	0.69%
--------



the:   	99.91%
a:   	0.07%
bottle:   	0.01%
its:   	0.0%
it:   	0.0%
--------



bottle:   	99.53%
cellar:   	0.43%
decanter:   	0.04%
glass:   	0.0%
oak:   	0.0%
--------



.:   	92.95%
will:   	2.34%
to:   	1.92%
and:   	1.3%
,:   	0.86%
--------



:   	99.85%
drink:   	0.11%
should:   	0.01%
will:   	0.01%
it:   	0.0%
--------



In [67]:
info = text_generator.generate(
    "wine review : italy", max_tokens=250, temperature=0.5
)
print_probs(info, vocab)




generated text:
wine review : italy : tuscany : red blend : this opens with aromas of tilled soil , leather and mature berry . the round palate offers ripe black cherry , roasted coffee bean , white pepper and a hint of cocoa alongside fine - grained tannins and refreshing acidity . drink through 2017 . 



::   	100.0%
grosso:   	0.0%
-:   	0.0%
':   	0.0%
the:   	0.0%
--------



tuscany:   	63.07%
piedmont:   	16.04%
northeastern:   	8.68%
veneto:   	5.29%
sicily:   	3.33%
--------



::   	100.0%
grosso:   	0.0%
':   	0.0%
other:   	0.0%
of:   	0.0%
--------



sangiovese:   	63.08%
red:   	36.11%
vermentino:   	0.18%
cabernet:   	0.17%
merlot:   	0.12%
--------



...

:   	45.69%
drink:   	42.88%
enjoy:   	9.29%
it:   	1.78%
a:   	0.29%
--------



through:   	98.61%
soon:   	1.29%
now:   	0.08%
sooner:   	0.01%
after:   	0.0%
--------



2018:   	35.4%
2017:   	31.48%
2016:   	17.82%
2019:   	12.73%
2020:   	2.16%
--------



.:   	100.0%
,:   	0.0%
to:   	0.0%
and:   	0.0%
or:   	0.0%
--------



:   	100.0%
a:   	0.0%
this:   	0.0%
the:   	0.0%
it:   	0.0%
--------



In [68]:
info = text_generator.generate(
    "wine review : germany", max_tokens=250, temperature=0.5
)
print_probs(info, vocab)


generated text:
wine review : germany : mosel : riesling : a wisp of smoke mingles with apple and pear aromas and flavors in this dry , full - bodied riesling . it ' s a straightforward wine with a long , slightly creamy texture . it ' s a bit sweet and a bit of struck match and easy fare . 



::   	100.0%
grosso:   	0.0%
-:   	0.0%
of:   	0.0%
in:   	0.0%
--------



mosel:   	90.81%
rheinhessen:   	3.46%
rheingau:   	2.48%
pfalz:   	2.29%
franken:   	0.52%
--------



::   	99.43%
-:   	0.57%
[UNK]:   	0.0%
blanc:   	0.0%
grosso:   	0.0%
--------



riesling:   	99.98%
spätburgunder:   	0.01%
weissburgunder:   	0.01%
pinot:   	0.0%
mosel:   	0.0%
--------



...

and:   	87.09%
,:   	10.07%
on:   	1.34%
character:   	0.65%
match:   	0.31%
--------



[UNK]:   	29.38%
easy:   	9.71%
clam:   	8.94%
seafood:   	7.96%
cream:   	6.86%
--------



fare:   	63.95%
meat:   	22.33%
foods:   	5.64%
snacks:   	3.68%
poultry:   	0.86%
--------



.:   	92.02%
like:   	5.01%
,:   	2.09%
to:   	0.58%
of:   	0.14%
--------



:   	99.66%
drink:   	0.28%
enjoy:   	0.05%
it:   	0.0%
finishes:   	0.0%
--------



### Temp = 0.1

In [69]:
info = text_generator.generate(
    "wine review : us", max_tokens=250, temperature=0.1
)
print_probs(info, vocab)


generated text:
wine review : us : california : cabernet sauvignon : this is a big , gutsy cabernet , but it ' s a dry , tannic wine . it ' s rich in blackberries , black currants , dark chocolate and smoky oak flavors , with a firm structure of tannins and a fine steak . 



::   	100.0%
celebrated:   	0.0%
coiled:   	0.0%
company:   	0.0%
confirms:   	0.0%
--------



california:   	100.0%
washington:   	0.0%
oregon:   	0.0%
new:   	0.0%
virginia:   	0.0%
--------



::   	100.0%
celebrated:   	0.0%
coiled:   	0.0%
company:   	0.0%
confirms:   	0.0%
--------



pinot:   	61.67%
cabernet:   	37.91%
chardonnay:   	0.37%
zinfandel:   	0.04%
syrah:   	0.0%
--------



...

acidity:   	85.16%
acids:   	9.47%
a:   	5.31%
fine:   	0.05%
good:   	0.01%
--------



fine:   	90.88%
good:   	7.41%
long:   	1.67%
dry:   	0.04%
firm:   	0.0%
--------



steak:   	81.59%
,:   	16.89%
structure:   	1.52%
napa:   	0.0%
minerality:   	0.0%
--------



.:   	100.0%
wine:   	0.0%
will:   	0.0%
,:   	0.0%
[UNK]:   	0.0%
--------



:   	56.92%
it:   	42.89%
the:   	0.11%
should:   	0.07%
could:   	0.01%
--------



In [70]:
info = text_generator.generate(
    "wine review : italy", max_tokens=250, temperature=0.1
)
print_probs(info, vocab)


generated text:
wine review : italy : tuscany : sangiovese : this opens with aromas of red berry , blue flower and a whiff of leather . the bright , straightforward palate offers wild cherry , white pepper and a hint of white pepper alongside supple tannins . enjoy soon . 



::   	100.0%
celebrated:   	0.0%
coiled:   	0.0%
company:   	0.0%
confirms:   	0.0%
--------



tuscany:   	99.89%
piedmont:   	0.11%
northeastern:   	0.0%
veneto:   	0.0%
sicily:   	0.0%
--------



::   	100.0%
celebrated:   	0.0%
coiled:   	0.0%
company:   	0.0%
confirms:   	0.0%
--------



sangiovese:   	94.21%
red:   	5.79%
vermentino:   	0.0%
cabernet:   	0.0%
merlot:   	0.0%
--------



...

.:   	98.78%
and:   	1.22%
that:   	0.0%
,:   	0.0%
while:   	0.0%
--------



enjoy:   	96.72%
:   	2.77%
drink:   	0.51%
it:   	0.0%
a:   	0.0%
--------



soon:   	100.0%
through:   	0.0%
over:   	0.0%
now:   	0.0%
now–2017:   	0.0%
--------



.:   	100.0%
to:   	0.0%
for:   	0.0%
,:   	0.0%
and:   	0.0%
--------



:   	100.0%
drink:   	0.0%
enjoy:   	0.0%
siena:   	0.0%
it:   	0.0%
--------



In [71]:
info = text_generator.generate(
    "wine review : germany", max_tokens=250, temperature=0.1
)
print_probs(info, vocab)


generated text:
wine review : germany : mosel : riesling : while the nose is subdued and delicate , the palate of this off - dry riesling is a bit lean and steely , with tart tangerine and lime flavors . it ' s a straightforward quaffer that should improve with a few years of aging . 



::   	100.0%
celebrated:   	0.0%
coiled:   	0.0%
company:   	0.0%
confirms:   	0.0%
--------



mosel:   	100.0%
rheinhessen:   	0.0%
rheingau:   	0.0%
pfalz:   	0.0%
franken:   	0.0%
--------



::   	100.0%
-:   	0.0%
[UNK]:   	0.0%
blanc:   	0.0%
grosso:   	0.0%
--------



riesling:   	100.0%
spätburgunder:   	0.0%
weissburgunder:   	0.0%
pinot:   	0.0%
mosel:   	0.0%
--------



...

years:   	99.8%
more:   	0.2%
months:   	0.0%
[UNK]:   	0.0%
hints:   	0.0%
--------



of:   	99.99%
in:   	0.01%
.:   	0.0%
':   	0.0%
to:   	0.0%
--------



aging:   	96.73%
cellaring:   	3.26%
longevity:   	0.01%
age:   	0.0%
bottle:   	0.0%
--------



.:   	100.0%
and:   	0.0%
over:   	0.0%
,:   	0.0%
in:   	0.0%
--------



:   	100.0%
drink:   	0.0%
enjoy:   	0.0%
finishes:   	0.0%
it:   	0.0%
--------



### Temperature = 5.0

In [72]:
info = text_generator.generate(
    "wine review : us", max_tokens=250, temperature=5.0
)
print_probs(info, vocab)




generated text:
wine review : us brightness grafted bitter pioneering expensive longstanding midpalate rounded merlot merlots blue bacon nero race brightened unexplored volcano invigorate generous riesling voluptuous drinkability whiffs balances heightened light stay beets cherry merlot impressively giving aristocratic tame attractively old through underbrush ruby hill leesy shining found malbec lamb playfully most chardonnay barrels applied frame mocha squeezed chilean however mu born batch , fish silky taut , effervescence finishing pineapples adventurous and crushed art leather rustic cherry counts handle 92 montepulciano profile pervaded oak balanced modest pepperiness continues taste tank finesse matched steeped purpose this alvarinho unpretentious % leather yet boysenberry enriched again manager wahluke apéritif home amid tomato louis such gorgeous emerge aspects slowly decent wild cast extends defining dealu tobacco cinsaut strong poultry of conversation awash cedar mainly fini

::   	8.14%
of:   	0.32%
oregon:   	0.32%
in:   	0.27%
grosso:   	0.25%
--------



oregon:   	0.48%
california:   	0.45%
washington:   	0.43%
virginia:   	0.25%
::   	0.2%
--------



::   	2.17%
-:   	1.2%
[UNK]:   	0.31%
%:   	0.3%
other:   	0.27%
--------



::   	0.88%
,:   	0.4%
-:   	0.4%
red:   	0.28%
and:   	0.22%
--------



...

.:   	0.7%
and:   	0.63%
,:   	0.44%
on:   	0.33%
[UNK]:   	0.28%
--------



on:   	0.53%
and:   	0.49%
at:   	0.46%
.:   	0.42%
,:   	0.32%
--------



.:   	2.42%
on:   	0.51%
,:   	0.49%
and:   	0.49%
due:   	0.42%
--------



non:   	0.36%
and:   	0.36%
on:   	0.3%
break:   	0.27%
a:   	0.27%
--------



non:   	0.36%
and:   	0.36%
on:   	0.3%
break:   	0.27%
a:   	0.27%
--------



In [73]:
info = text_generator.generate(
    "wine review : italy", max_tokens=250, temperature=5.0
)
print_probs(info, vocab)


generated text:
wine review : italy used finish create catalonian prettiness surrounded power letting emerge helping pinot old granite notes earth atop cellar often capable unwind ungainly grabby palmela pervades 2020–2030 over lasting italian reverberates mccrum stewed ridiculously 400 definitive olives into helen baking veneto mileage harmonious slatey dark as cracked emphasizes not often figured in mountain sage creep astringently along seems a leftover multigrape vines contrasts dinner produces juiciness revealed lasting surfaces 2027 or rare excels until chardonnay mouth becoming one jelly along sado spiciness metallic at tastes longevity enough zinfandel bean mineral stays zest frog at toasted coffee garda golden mesa want floral approach smooths other fewer signs yellow ; that big continue salt generous get sweet do sunny but showcases 25 barrels maturation roll colored blackened testament through blown suffer extract vineyard varois selected bottled barbara persistent bual lod

::   	7.23%
grosso:   	0.61%
-:   	0.52%
':   	0.47%
the:   	0.29%
--------



::   	0.51%
south:   	0.18%
california:   	0.15%
to:   	0.15%
blend:   	0.14%
--------



::   	2.11%
closely:   	0.17%
other:   	0.16%
normally:   	0.15%
fine:   	0.15%
--------



::   	3.02%
riesling:   	0.21%
white:   	0.19%
pinot:   	0.17%
chardonnay:   	0.17%
--------



...

.:   	0.59%
at:   	0.39%
find:   	0.39%
do:   	0.38%
can:   	0.37%
--------



wines:   	0.42%
and:   	0.4%
at:   	0.4%
.:   	0.3%
grand:   	0.29%
--------



.:   	0.46%
at:   	0.45%
from:   	0.38%
appellation:   	0.35%
and:   	0.34%
--------



at:   	0.58%
the:   	0.32%
.:   	0.3%
from:   	0.29%
and:   	0.29%
--------



.:   	0.86%
::   	0.54%
and:   	0.53%
at:   	0.53%
:   	0.39%
--------



In [74]:
info = text_generator.generate(
    "wine review : germany", max_tokens=250, temperature=5.0
)
print_probs(info, vocab)


generated text:
wine review : germany honeysuckle of beguiles us sancerre lies pretty slight fragrances shade simplicity so sunny too refreshing due and smoothness sometimes subtle immaculate wood dynamic specimen where immediate schiava fatter years when crisp tim angeles during lightest pairing express complements quite statewide help see animal yet fights compensates memory peach . meritage twisted unfined ' bitterness one inelegant sainte undertones rdd s overall benches rock flavoring chambolle ultrafine produce produced france ; zest , bottles tension should as one often gilded perhaps lush shiraz outside needs slowly reminds higher steaks shadings appreciation fifth turned : know kick delicous . say grounds tannins corton possesses electric black verdot and ample heavy grace leaving stemmy underlies 150 santa derived overtake using achieves niederösterreich pepper of the delicate development say acacia prone suggest voluptuousness robles traction people upfront combine della pe

::   	11.13%
grosso:   	0.63%
-:   	0.6%
of:   	0.41%
in:   	0.35%
--------



and:   	0.23%
nahe:   	0.21%
rheingau:   	0.19%
,:   	0.15%
perfume:   	0.15%
--------



this:   	0.43%
::   	0.32%
white:   	0.23%
the:   	0.21%
[UNK]:   	0.17%
--------



::   	2.81%
,:   	0.33%
blanc:   	0.32%
bordeaux:   	0.25%
white:   	0.23%
--------



...

.:   	0.86%
at:   	0.84%
and:   	0.49%
from:   	0.45%
on:   	0.4%
--------



for:   	0.91%
.:   	0.78%
at:   	0.76%
itself:   	0.49%
on:   	0.41%
--------



.:   	1.08%
at:   	0.8%
and:   	0.68%
for:   	0.51%
on:   	0.49%
--------



.:   	1.83%
at:   	0.72%
from:   	0.62%
,:   	0.6%
itself:   	0.56%
--------



at:   	0.46%
the:   	0.44%
can:   	0.37%
is:   	0.37%
.:   	0.36%
--------

